In [1]:
# Imports

In [50]:
# File names
# HL, 0 and 01, for NL <—> LI,
path_0 = "/Users/Suzenator/Documents/Uni/M4/MThesis/output/backup/total/high_low/01_gpt-mt/supervised/"
path_01 = "/Users/Suzenator/Documents/Uni/M4/MThesis/output/backup/total/high_low/0_gpt-mt/supervised/"
nl_file_hyp = "lim_Latn.devtest.lim2nld_translation"
li_file_hyp = "nld_Latn.devtest.nld2lim_translation"

path_test = "/Users/Suzenator/Documents/Uni/M4/MThesis/Data/flores_subset/devtest_original/"
li_test = "lim_Latn.devtest"
nl_test = "nld_Latn.devtest"
en_test = "eng_Latn.devtest"

In [20]:
# Load files
with open(path_01+nl_file) as fp:
    nl_01_hyp = fp.readlines()

with open(path_0+nl_file) as fp:
    nl_0_hyp = fp.readlines()
    
with open(path_01+li_file) as fp:
    li_01_hyp = fp.readlines()
    
with open(path_0+li_file) as fp:
    li_0_hyp = fp.readlines()

with open(path_test+li_test) as fp:
    li_src = fp.readlines()
    
with open(path_test+nl_test) as fp:
    nl_src = fp.readlines()

In [21]:
# Combine into structured dataset
data = []

# Pair hypotheses with sources and references
for i in range(len(nl_src)):  # Assuming all lists have the same length
    # For Dutch hypotheses
    data.append({
        "source": nl_src[i],      # Source sentence in Dutch
        "output": nl_01_hyp[i],   # Hypothesis from system 01 (Dutch)
        "reference": nl_src[i],   # Reference translation (Dutch)
    })
    data.append({
        "source": nl_src[i],      # Source sentence in Dutch
        "output": nl_0_hyp[i],    # Hypothesis from system 0 (Dutch)
        "reference": nl_src[i],   # Reference translation (Dutch)
    })
    
    # For Limburgish hypotheses
    data.append({
        "source": li_src[i],      # Source sentence in Limburgish
        "output": li_01_hyp[i],   # Hypothesis from system 01 (Limburgish)
        "reference": li_src[i],   # Reference translation (Limburgish)
    })
    data.append({
        "source": li_src[i],      # Source sentence in Limburgish
        "output": li_0_hyp[i],    # Hypothesis from system 0 (Limburgish)
        "reference": li_src[i],   # Reference translation (Limburgish)
    })

# Example print
print(f"Dataset size: {len(data)}")
print(f"Example entry: {data[0]}")

Dataset size: 4048
Example entry: {'source': "'Inmiddels hebben we muizen van 4 maanden oud die geen diabetes hebben, maar dat eerder wel hebben,' voegde hij er nog aan toe. \n", 'output': '“Ik heb al vier maanden een muis die geen diabetes heeft, maar wel iers diabetes had,” vertelde hij.\n', 'reference': "'Inmiddels hebben we muizen van 4 maanden oud die geen diabetes hebben, maar dat eerder wel hebben,' voegde hij er nog aan toe. \n"}


In [25]:
def detect_duplication(output: str) -> [str]:
    """Detect repeated words or phrases in the output."""
    words = output.split()
    ngrams = [' '.join(words[i:i+2]) for i in range(len(words)-1)]  # Bigrams
    duplicates = {ngram for ngram in ngrams if ngrams.count(ngram) > 1}
    return list(duplicates)

# Test duplication detection
for entry in data:
    duplicates = detect_duplication(entry["output"])
    if duplicates:
        print(f"**Duplication found:** {duplicates}")
        print(f"Output: {entry['output']}\n")

**Duplication found:** ['van de']
Output: Dr. Ehud Ur, professor medicijnen aan Dalhousie University in Halifax, Nova Scoatia en voorzitter van de klinische en wetenschappelijke commissie van de Canadian Diabetes Association, waarschuwde dat het nog altijd vreug in het onderzoek is.


**Duplication found:** ['van de']
Output: Dr. Ehud Ur, professor medicijnen aan Dalhousie University in Halifax, Nova Scotia, en voorzitter van de klinische en wetenschappelijke commissie van de Canadian Diabetes Association, waarschuwde dat het nog altijd in het oog is.


**Duplication found:** ['van de']
Output: Professor Ehud Ur in de geneeskunde aan Dalhousie University in Halifax, Nova Scotia, tevens voorzitter van de klinische en wetenschappelijke divisie van de Canadian Diabetes Association, herinnerde eraan dat ze nog maar net zijn begonnen met het onderzoek.


**Duplication found:** ['van de']
Output: Professor Ehud Ur in de geneeskunde aan Dalhousie University in Halifax, Nova Scotia, tevens voo

In [26]:
def detect_length_mismatch(output: str, reference: str) -> bool:
    """Flag sentences where output and reference lengths differ significantly."""
    len_output = len(output.split())
    len_reference = len(reference.split())
    return abs(len_output - len_reference) > 3  # Threshold for mismatch

# Test length mismatch detection
for entry in data:
    if detect_length_mismatch(entry["output"], entry["reference"]):
        print(f"**Length Mismatch:**")
        print(f"Output: {entry['output']}")
        print(f"Reference: {entry['reference']}\n")


**Length Mismatch:**
Output: “Ik heb al vier maanden een muis die geen diabetes heeft, maar wel iers diabetes had,” vertelde hij.

Reference: 'Inmiddels hebben we muizen van 4 maanden oud die geen diabetes hebben, maar dat eerder wel hebben,' voegde hij er nog aan toe. 


**Length Mismatch:**
Output: Dr. Ehud Ur, professor medicijnen aan Dalhousie University in Halifax, Nova Scotia, en voorzitter van de klinische en wetenschappelijke commissie van de Canadian Diabetes Association, waarschuwde dat het nog altijd in het oog is.

Reference: Professor Ehud Ur in de geneeskunde aan Dalhousie University in Halifax, Nova Scotia, tevens voorzitter van de klinische en wetenschappelijke divisie van de Canadian Diabetes Association, herinnerde eraan dat ze nog maar net zijn begonnen met het onderzoek.


**Length Mismatch:**
Output: Jus wie sommege aandere experts is heer sceptisch of sukkerzìkde geneze kin weure, drop wiezend da dees bevindinge neet relevant zien veur lui die al sukkerzìkde Type 

In [ ]:
def analyze_errors(data: [dict]) -> [dict]:
    """Analyze and aggregate errors for manual review."""
    results = []
    for entry in data:
        result = {
            "source": entry["source"],
            "output": entry["output"],
            "reference": entry["reference"],
            "errors": []
        }
        # Check for duplication
        duplicates = detect_duplication(entry["output"])
        if duplicates:
            result["errors"].append({"type": "duplication", "details": duplicates})
        
        # Check for length mismatch
        if detect_length_mismatch(entry["output"], entry["reference"]):
            result["errors"].append({"type": "length_mismatch"})
        
        results.append(result)
    return results

# Run analysis and print results
error_analysis = analyze_errors(data)
for entry in error_analysis:
    if entry["errors"]:
        print(f"Source: {entry['source']}")
        print(f"Output: {entry['output']}")
        print(f"Reference: {entry['reference']}")
        print(f"Errors: {entry['errors']}\n")


Source: 'Inmiddels hebben we muizen van 4 maanden oud die geen diabetes hebben, maar dat eerder wel hebben,' voegde hij er nog aan toe. 

Output: “Ik heb al vier maanden een muis die geen diabetes heeft, maar wel iers diabetes had,” vertelde hij.

Reference: 'Inmiddels hebben we muizen van 4 maanden oud die geen diabetes hebben, maar dat eerder wel hebben,' voegde hij er nog aan toe. 

Errors: [{'type': 'length_mismatch'}]

Source: Professor Ehud Ur in de geneeskunde aan Dalhousie University in Halifax, Nova Scotia, tevens voorzitter van de klinische en wetenschappelijke divisie van de Canadian Diabetes Association, herinnerde eraan dat ze nog maar net zijn begonnen met het onderzoek.

Output: Dr. Ehud Ur, professor medicijnen aan Dalhousie University in Halifax, Nova Scoatia en voorzitter van de klinische en wetenschappelijke commissie van de Canadian Diabetes Association, waarschuwde dat het nog altijd vreug in het onderzoek is.

Reference: Professor Ehud Ur in de geneeskunde aan Dal

In [31]:
def extract_representative_examples(errors: [dict], error_type: str, max_examples: int = 3) -> [dict]:
    """Extract representative examples for a specific error type."""
    examples = [entry for entry in errors if any(err["type"] == error_type for err in entry["errors"])]
    return examples[:max_examples]

# Example: Get representative examples for duplication errors
duplication_examples = extract_representative_examples(error_analysis, "duplication")
print("Representative Examples for Duplication:")
for example in duplication_examples:
    print(f"Source: {example['source']}")
    print(f"Output: {example['output']}")
    print(f"Reference: {example['reference']}")
    print(f"Errors: {example['errors']}\n")


Representative Examples for Duplication:
Source: Professor Ehud Ur in de geneeskunde aan Dalhousie University in Halifax, Nova Scotia, tevens voorzitter van de klinische en wetenschappelijke divisie van de Canadian Diabetes Association, herinnerde eraan dat ze nog maar net zijn begonnen met het onderzoek.

Output: Dr. Ehud Ur, professor medicijnen aan Dalhousie University in Halifax, Nova Scoatia en voorzitter van de klinische en wetenschappelijke commissie van de Canadian Diabetes Association, waarschuwde dat het nog altijd vreug in het onderzoek is.

Reference: Professor Ehud Ur in de geneeskunde aan Dalhousie University in Halifax, Nova Scotia, tevens voorzitter van de klinische en wetenschappelijke divisie van de Canadian Diabetes Association, herinnerde eraan dat ze nog maar net zijn begonnen met het onderzoek.

Errors: [{'type': 'duplication', 'details': ['van de']}]

Source: Professor Ehud Ur in de geneeskunde aan Dalhousie University in Halifax, Nova Scotia, tevens voorzitter v

In [65]:
# Function to analyze errors for both systems
def analyze_errors_grouped(data: List[Dict[str, Any]]) -> List[Dict[str, Any]]:
    """
    Analyze a dataset where each entry has outputs for system_0 and system_01.
    
    Args:
        data: A list of dictionaries, each with 'source', 'reference', and 'systems' outputs.
        
    Returns:
        A list of dictionaries with error annotations for both systems and a comparison.
    """
    results = []
    
    for entry in data:
        # Analyze errors for each system
        errors_0 = detect_errors(entry["systems"]["system_0"], entry["reference"])
        errors_01 = detect_errors(entry["systems"]["system_01"], entry["reference"])
        
        # Identify common and unique errors
        common_errors = [err for err in errors_0 if err in errors_01]
        unique_0 = [err for err in errors_0 if err not in errors_01]
        unique_01 = [err for err in errors_01 if err not in errors_0]
        
        # Append analysis
        results.append({
            "source_language": entry["source_language"],
            "target_language": entry["target_language"],
            "source": entry["source"],
            "reference": entry["reference"],
            "systems": entry["systems"],
            "English": entry["English"],
            "errors": {
                "system_0": errors_0,
                "system_01": errors_01,
                "common": common_errors,
                "unique_0": unique_0,
                "unique_01": unique_01,
            }
        })
    
    return results

# Detect errors for a single system
def detect_errors(output: str, reference: str) -> List[Dict[str, Any]]:
    """
    Detect all errors (duplication, length mismatch, mistranslation) in a single output.
    
    Args:
        output: The output sentence to analyze.
        reference: The reference sentence.
        
    Returns:
        A list of error dictionaries.
    """
    errors = []
    
    # Duplication detection
    duplicates = detect_duplication(output)
    if duplicates:
        errors.append({"type": "duplication", "details": duplicates})
    
    # Length mismatch detection
    if detect_length_mismatch(output, reference):
        errors.append({"type": "length_mismatch"})
    
    # Mistranslation detection
    if detect_mistranslation(output, reference):
        errors.append({"type": "mistranslation"})
    
    return errors

# Print detailed error report
def print_detailed_error_report(results: List[Dict[str, Any]]):
    """
    Print a detailed error analysis report for both systems.
    
    Args:
        results: A list of error-annotated entries from analyze_errors_grouped.
    """
    print("Detailed Error Analysis Report")
    print("=============================\n")
    for entry in results:
        print(f"Source Language: {entry['source_language']}")
        print(f"Target Language: {entry['target_language']}")
        print(f"Source: {entry['source']}")
        print(f"Reference: {entry['reference']}")
        print(f"English: {entry['English']}\n")
        print(f"System 0 Output: {entry['systems']['system_0']}")
        print(f"System 01 Output: {entry['systems']['system_01']}\n")
        
        # Error details
        print("Errors:")
        print(f"  - System 0: {entry['errors']['system_0']}")
        print(f"  - System 01: {entry['errors']['system_01']}")
        print(f"  - Common Errors: {entry['errors']['common']}")
        print(f"  - Unique to System 0: {entry['errors']['unique_0']}")
        print(f"  - Unique to System 01: {entry['errors']['unique_01']}\n")
        print("-----------------------------\n")


In [66]:
# Load files and strip whitespace
with open(path_01 + nl_file) as fp:
    nl_01_hyp = [line.strip() for line in fp.readlines()]  # Hypothesis 01 (NL)

with open(path_0 + nl_file) as fp:
    nl_0_hyp = [line.strip() for line in fp.readlines()]  # Hypothesis 0 (NL)

with open(path_01 + li_file) as fp:
    li_01_hyp = [line.strip() for line in fp.readlines()]  # Hypothesis 01 (LI)

with open(path_0 + li_file) as fp:
    li_0_hyp = [line.strip() for line in fp.readlines()]  # Hypothesis 0 (LI)

with open(path_test + li_test) as fp:
    li_src = [line.strip() for line in fp.readlines()]  # Source (LI)

with open(path_test + nl_test) as fp:
    nl_src = [line.strip() for line in fp.readlines()]  # Source (NL)
    
with open(path_test + en_test) as fp:
    en_src = [line.strip() for line in fp.readlines()]  # Source (EN)

# Combine into structured dataset
data = []

# Pair hypotheses with sources and references for each sentence
for i in range(len(nl_src)):  # Assuming all lists have the same length
    # Dutch sentences
    data.append({
        "source_language": "Limburgish",
        "target_language": "Dutch",
        "source": li_src[i],      # Source sentence in Limburgish
        "reference": nl_src[i],   # Reference translation (Dutch)
        "English": en_src[i],
        "systems": {
            "system_0": nl_0_hyp[i],  # Output from system 0 (Dutch)
            "system_01": nl_01_hyp[i]  # Output from system 01 (Dutch)
        }
    })
    
    # Limburgish sentences
    data.append({
        "source_language": "Dutch",
        "target_language": "Limburgish",
        "source": nl_src[i],      # Source sentence in Dutch
        "reference": li_src[i],   # Reference translation (Limburgish)
        "English": en_src[i],
        "systems": {
            "system_0": li_0_hyp[i],  # Output from system 0 (Limburgish)
            "system_01": li_01_hyp[i]  # Output from system 01 (Limburgish)
        }
    })

# Example print
print(f"Dataset size: {len(data)}")
print(f"Example entry: {data[0]}")

Dataset size: 2024
Example entry: {'source_language': 'Limburgish', 'target_language': 'Dutch', 'source': '“Veer höbbe noe muis vaan 4 maond aajd die gein diabetes höbbe mer wel iers diabetes hadde,” veugde heer touw.', 'reference': "'Inmiddels hebben we muizen van 4 maanden oud die geen diabetes hebben, maar dat eerder wel hebben,' voegde hij er nog aan toe.", 'English': '"We now have 4-month-old mice that are non-diabetic that used to be diabetic," he added.', 'systems': {'system_0': '“Ik heb een paar maanden geleden een muis gekregen die geen diabetes had, maar wel diabetes had gekregen,” zei hij.', 'system_01': '“Ik heb al vier maanden een muis die geen diabetes heeft, maar wel iers diabetes had,” vertelde hij.'}}


In [67]:
results = analyze_errors_grouped(data)

In [ ]:
print_detailed_error_report(results)

Detailed Error Analysis Report

Source Language: Limburgish
Target Language: Dutch
Source: “Veer höbbe noe muis vaan 4 maond aajd die gein diabetes höbbe mer wel iers diabetes hadde,” veugde heer touw.
Reference: 'Inmiddels hebben we muizen van 4 maanden oud die geen diabetes hebben, maar dat eerder wel hebben,' voegde hij er nog aan toe.
English: "We now have 4-month-old mice that are non-diabetic that used to be diabetic," he added.

System 0 Output: “Ik heb een paar maanden geleden een muis gekregen die geen diabetes had, maar wel diabetes had gekregen,” zei hij.
System 01 Output: “Ik heb al vier maanden een muis die geen diabetes heeft, maar wel iers diabetes had,” vertelde hij.

Errors:
  - System 0: [{'type': 'mistranslation'}]
  - System 01: [{'type': 'length_mismatch'}, {'type': 'mistranslation'}]
  - Common Errors: [{'type': 'mistranslation'}]
  - Unique to System 0: []
  - Unique to System 01: [{'type': 'length_mismatch'}]

-----------------------------

Source Language: Dutc

In [49]:
duplication_examples = extract_representative_examples(error_analysis, "duplication")
print("Representative Examples for Duplication:")
for example in duplication_examples:
    print(f"Source Language: {example['source_language']}")
    print(f"Target Language: {example['target_language']}")
    print(f"Source: {example['source']}")
    print(f"Output: {example['output']}")
    print(f"Reference: {example['reference']}")
    print(f"Errors: {example['errors']}\n")

Representative Examples for Duplication:
Source Language: Dutch
Target Language: Dutch
Source: Professor Ehud Ur in de geneeskunde aan Dalhousie University in Halifax, Nova Scotia, tevens voorzitter van de klinische en wetenschappelijke divisie van de Canadian Diabetes Association, herinnerde eraan dat ze nog maar net zijn begonnen met het onderzoek.
Output: Dr. Ehud Ur, professor medicijnen aan Dalhousie University in Halifax, Nova Scoatia en voorzitter van de klinische en wetenschappelijke commissie van de Canadian Diabetes Association, waarschuwde dat het nog altijd vreug in het onderzoek is.
Reference: Professor Ehud Ur in de geneeskunde aan Dalhousie University in Halifax, Nova Scotia, tevens voorzitter van de klinische en wetenschappelijke divisie van de Canadian Diabetes Association, herinnerde eraan dat ze nog maar net zijn begonnen met het onderzoek.
Errors: [{'type': 'duplication', 'details': ['van de']}, {'type': 'mistranslation'}]

Source Language: Dutch
Target Language: Du